# Creating Yolo dataset

## Moving images to the yolo dataset folder

In [1]:
import os
import shutil

# Paths to source folders
train_folder = 'input/gtsrb-german-traffic-sign/Train'
test_folder = 'input/gtsrb-german-traffic-sign/Test'

# Destination folder
destination_folder = 'yolo_dataset/images'

# Ensuring the destination folder exists
if not os.path.exists(destination_folder):
    os.makedirs(destination_folder)

def copy_images(source, destination):
    for root, dirs, files in os.walk(source):
        for file in files:
            # Checking if the file is an image by extension
            if file.lower().endswith(('.png', '.jpg', '.jpeg')):
                source_path = os.path.join(root, file)
                dest_path = os.path.join(destination, file)
                
                # Copying the file to the destination
                shutil.copy2(source_path, dest_path)

# Copying images from both the Train and Test folders
copy_images(train_folder, destination_folder)
copy_images(test_folder, destination_folder)

print("All images have been consolidated into:", destination_folder)

All images have been consolidated into: yolo_dataset/images


## Splitting train and validation data

In [1]:
import os
import shutil

source_folder = 'yolo_dataset/images'  # where the images currently reside

train_folder = 'yolo_dataset/images/train'
val_folder = 'yolo_dataset/images/val'

# Ensuring the train and val folders exist
os.makedirs(train_folder, exist_ok=True)
os.makedirs(val_folder, exist_ok=True)

# Listing all files in the source folder (excluding train/val subdirectories, if already created)
for file_name in os.listdir(source_folder):
    source_path = os.path.join(source_folder, file_name)

    # Skipping subdirectories or non-image files if present
    if os.path.isdir(source_path):
        continue

    # Checking if the filename contains an underscore
    if '_' in file_name:
        dest_path = os.path.join(train_folder, file_name)
    else:
        dest_path = os.path.join(val_folder, file_name)

    # Moving the file to the appropriate folder
    shutil.move(source_path, dest_path)

## Creating labels from existing csv files, in the yolo format

In [3]:
import os
import csv

# Paths to the CSV files
train_csv_path = 'input/gtsrb-german-traffic-sign/Train.csv'
test_csv_path = 'input/gtsrb-german-traffic-sign/Test.csv'

# Destination folder for YOLO label files
labels_folder = 'yolo_dataset/labels'

# Ensuring the labels folder exists
if not os.path.exists(labels_folder):
    os.makedirs(labels_folder)

def process_csv_and_create_labels(csv_file):
    with open(csv_file, mode='r', newline='', encoding='utf-8') as f:
        reader = csv.DictReader(f)
        
        for row in reader:
            # Extracting relevant columns
            img_width = float(row['Width'])
            img_height = float(row['Height'])
            x1 = float(row['Roi.X1'])
            y1 = float(row['Roi.Y1'])
            x2 = float(row['Roi.X2'])
            y2 = float(row['Roi.Y2'])
            class_id = row['ClassId']
            img_path = row['Path']  # e.g., 'Test/00000.png' or 'Train/20/00020_00000_00000.png'
            
            # Deriving bounding box center and size in pixels
            bbox_width = x2 - x1
            bbox_height = y2 - y1
            x_center = x1 + (bbox_width / 2)
            y_center = y1 + (bbox_height / 2)
            
            # Normalizing by the image dimensions
            x_center_norm = x_center / img_width
            y_center_norm = y_center / img_height
            w_norm = bbox_width / img_width
            h_norm = bbox_height / img_height
            
            # Building the label file name by extracting the base name (e.g., '00000.png' -> '00000.txt')
            file_name = os.path.splitext(os.path.basename(img_path))[0] + '.txt'
            label_file_path = os.path.join(labels_folder, file_name)
            
            # YOLO label format: class x_center y_center width height
            yolo_line = f"{class_id} {x_center_norm} {y_center_norm} {w_norm} {h_norm}\n"
            
            # Writing the label to a text file
            with open(label_file_path, 'a') as label_file:
                label_file.write(yolo_line)

# Processing both Train and Test CSV files
process_csv_and_create_labels(train_csv_path)
process_csv_and_create_labels(test_csv_path)

print("Label files have been generated in:", labels_folder)

Label files have been generated in: yolo_dataset/labels


## Splitting labels to train and validation data

In [ ]:
import os
import shutil

labels_source_folder = 'yolo_dataset/labels'  # where the label files currently reside

labels_train_folder = 'yolo_dataset/labels/train'
labels_val_folder = 'yolo_dataset/labels/val'

# Ensuring the train and val folders exist
os.makedirs(labels_train_folder, exist_ok=True)
os.makedirs(labels_val_folder, exist_ok=True)

# Iterating through the label files in the source folder
for file_name in os.listdir(labels_source_folder):
    source_path = os.path.join(labels_source_folder, file_name)

    # Skipping subdirectories or non-txt files if present
    if os.path.isdir(source_path) or not file_name.lower().endswith('.txt'):
        continue

    # Checking if the filename contains an underscore
    if '_' in file_name:
        dest_path = os.path.join(labels_train_folder, file_name)
    else:
        dest_path = os.path.join(labels_val_folder, file_name)

    # Moving the file to the appropriate folder
    shutil.move(source_path, dest_path)

# Generating a config yaml file

In [6]:
import os

# List of class names
classes = [
    "speed limit 20", "speed limit 30", "speed limit 50", "speed limit 60",
    "speed limit 70", "speed limit 80", "end of speed limit 80", "speed limit 100",
    "speed limit 120", "no overtaking", "no overtaking trucks", "crossroads",
    "main road", "give way", "stop and yeld", "stop", "no heavy vehicles",
    "no entry", "danger point", "curve left", "curve right", "double bend",
    "uneven road", "slippery road", "road narrows from right", "workers on the road",
    "traffic signal ahead", "pedestrians may cross", "children crossing",
    "bicycles crossing", "snow road", "animals crossing", "end of restrictions",
    "turn right", "turn left", "ahead only", "ahead or turn right",
    "ahead or turn left", "right pass", "left pass", "roundabout",
    "end of stop overtaking", "end of stop overtaking trucks", "speed limit 5",
    "speed limit 15", "no proceed straight", "no left turn", "no left and right turns",
    "no right turn", "no overtaking", "no u-turn", "no motor vehicles", "no honking",
    "end of maximum speed limit 40", "end of maximum speed limit 50",
    "turn left and/or right", "limited-access road", "honking allowed",
    "speed limit 40", "bicycles only", "u-turn", "no proceed straight and left turns",
    "no parking", "no stopping", "railroad crossing", "dead end", "falling rocks",
    "hospital", "no cycling", "two way traffic"
]

# Retrieving the current directory
current_dir = os.getcwd()

yaml_content = f"""path: {current_dir}
train: yolo_dataset/images/train
val: yolo_dataset/images/val
nc: {len(classes)}
names:
"""

for c in classes:
    yaml_content += f"  - {c}\n"

yaml_file_path = "yolo_model_config.yaml"

with open(yaml_file_path, 'w', encoding='utf-8') as yaml_file:
    yaml_file.write(yaml_content)

print("YAML file created at:", yaml_file_path)

YAML file created at: yolo_model_config.yaml


# Training a YOLO model

In [1]:
from ultralytics import YOLO

# Loading the YOLOv11 model
model = YOLO("yolo11n.pt")

# Training with the specified YAML configuration file
train_results = model.train(
    data="yolo_model_config.yaml",
    epochs=10,
    imgsz=640,
    device=0,       # Using GPU 0
    name="traffic"  # Saves checkpoints under the name 'traffic'
)

# Evaluating the model on the validation set
metrics = model.val()

# Performing object detection on sample images
results = model("val.jpg")
for r in results:
    r.show()

# Exporting the trained model in ONNX format
export_path = model.export(format="onnx", name="traffic")
print("Exported model path:", export_path)

New https://pypi.org/project/ultralytics/8.3.63 available  Update with 'pip install -U ultralytics'
Ultralytics 8.3.39  Python-3.11.9 torch-2.5.1+cu121 CUDA:0 (NVIDIA GeForce RTX 3050 Laptop GPU, 4096MiB)
engine\trainer: task=detect, mode=train, model=yolo11n.pt, data=yolo_model_config.yaml, epochs=10, time=None, patience=100, batch=16, imgsz=640, save=True, save_period=-1, cache=False, device=0, workers=8, project=None, name=traffic3, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=F

train: Scanning C:\Users\polat\Desktop\Traffic-Signs-Detection\yolo_dataset\labels\train... 42085 images, 0 backgrounds, 0 corrupt: 100%|██████████| 42085/42085 [00:30<00:00, 1383.95it/s]

train: WARNING  C:\Users\polat\Desktop\Traffic-Signs-Detection\yolo_dataset\images\train\00000_00000_00000.png: 1 duplicate labels removed
train: WARNING  C:\Users\polat\Desktop\Traffic-Signs-Detection\yolo_dataset\images\train\00000_00000_00001.png: 1 duplicate labels removed
train: WARNING  C:\Users\polat\Desktop\Traffic-Signs-Detection\yolo_dataset\images\train\00000_00000_00002.png: 1 duplicate labels removed
train: WARNING  C:\Users\polat\Desktop\Traffic-Signs-Detection\yolo_dataset\images\train\00000_00000_00003.png: 1 duplicate labels removed
train: WARNING  C:\Users\polat\Desktop\Traffic-Signs-Detection\yolo_dataset\images\train\00000_00000_00004.png: 1 duplicate labels removed
train: WARNING  C:\Users\polat\Desktop\Traffic-Signs-Detection\yolo_dataset\images\train\00000_00000_00005.png: 1 duplicate labels removed
train: WARNING  C:\Users\polat\Desktop\Traffic-Signs-Detection\yolo_dataset\images\train\00000_00000_00006.png: 1 duplicate labels removed
train: WARNING  C:\Users\po

train: New cache created: C:\Users\polat\Desktop\Traffic-Signs-Detection\yolo_dataset\labels\train.cache


c:\Users\polat\AppData\Local\Programs\Python\Python311\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


...

                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 432/432 [02:57<00:00,  2.43it/s]


                   all      13804      13897      0.925      0.844      0.895      0.827
        speed limit 20         60         60      0.977          1      0.995      0.933
        speed limit 30        720        720      0.987      0.999      0.989      0.935
        speed limit 50        750        750      0.988      0.993      0.994      0.951
        speed limit 60        450        450      0.979       0.98      0.993      0.935
        speed limit 70        660        660      0.995      0.975      0.995      0.926
        speed limit 80        630        630      0.968      0.995      0.994      0.936
 end of speed limit 80        150        150          1      0.879      0.955      0.876
       speed limit 100        450        450          1      0.997      0.995       0.93
       speed limit 120        450        450      0.995      0.944      0.988      0.916
         no overtaking        480        480      0.986          1      0.995      0.943
  no overtaking truck

val: Scanning C:\Users\polat\Desktop\Traffic-Signs-Detection\yolo_dataset\labels\val.cache... 13792 images, 12 backgrounds, 0 corrupt: 100%|██████████| 13804/13804 [00:00<?, ?it/s]
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 863/863 [12:20<00:00,  1.17it/s]


                   all      13804      13897      0.926      0.843      0.895      0.827
        speed limit 20         60         60      0.977          1      0.995      0.933
        speed limit 30        720        720      0.987      0.999      0.989      0.933
        speed limit 50        750        750      0.988      0.995      0.994       0.95
        speed limit 60        450        450      0.979       0.98      0.993      0.934
        speed limit 70        660        660      0.995      0.974      0.995      0.925
        speed limit 80        630        630      0.968      0.995      0.994      0.936
 end of speed limit 80        150        150          1      0.878      0.955      0.876
       speed limit 100        450        450          1      0.997      0.995       0.93
       speed limit 120        450        450      0.995      0.944      0.988      0.917
         no overtaking        480        480      0.986          1      0.995      0.943
  no overtaking truck

ImportError: DLL load failed while importing onnx_cpp2py_export: A dynamic link library (DLL) initialization routine failed.

# Testing the model

In [6]:
import os
import random
from ultralytics import YOLO
from PIL import Image

# Loading the trained YOLO model
model = YOLO("traffic.pt")

# Path to the test images
test_folder = 'input/gtsrb-german-traffic-sign/Test'

# Get the list of all test images
all_test_images = [os.path.join(test_folder, f) for f in os.listdir(test_folder) if f.lower().endswith(('.png', '.jpg', '.jpeg'))]

# Select the last 1000 test images
last_1000_test_images = all_test_images[-1000:]

# Randomly select 20 images from the last 1000 test images
random_20_images = random.sample(last_1000_test_images, 20)

# Apply the model to the selected images and visualize the predictions
for img_path in random_20_images:
    results = model(img_path)
    for r in results:
        r.show()



image 1/1 c:\Users\polat\Desktop\Traffic-Signs-Detection\input\gtsrb-german-traffic-sign\Test\12827.png: 576x640 1 no left turn, 67.0ms
Speed: 5.0ms preprocess, 67.0ms inference, 2.0ms postprocess per image at shape (1, 3, 576, 640)

image 1/1 c:\Users\polat\Desktop\Traffic-Signs-Detection\input\gtsrb-german-traffic-sign\Test\13400.png: 640x640 1 u-turn, 33.0ms
Speed: 5.0ms preprocess, 33.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 c:\Users\polat\Desktop\Traffic-Signs-Detection\input\gtsrb-german-traffic-sign\Test\13788.png: 640x640 (no detections), 11.0ms
Speed: 4.0ms preprocess, 11.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 c:\Users\polat\Desktop\Traffic-Signs-Detection\input\gtsrb-german-traffic-sign\Test\13789.png: 640x640 (no detections), 13.8ms
Speed: 3.2ms preprocess, 13.8ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 c:\Users\polat\Desktop\Traffic-Signs-Detection\input\gtsr